<a href="https://colab.research.google.com/github/Sowndharyaramanadhan/Video-Summarization/blob/main/Video_Summarization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
video_file_name = "/content/drive/MyDrive/MS Dhoni's Vande Mataram World Cup Moment! 🇮🇳.mp4"# @param

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
!apt install -q ffmpeg
!pip install -q ffpb

Reading package lists...
Building dependency tree...
Reading state information...
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.


In [5]:
import os
import librosa
import tempfile
import librosa
from time import strftime, gmtime
from moviepy.editor import VideoFileClip
from IPython.display import Audio, HTML
from transformers import WhisperProcessor, WhisperForConditionalGeneration
from google.colab import userdata

from IPython.display import HTML
from base64 import b64encode


import google.generativeai as genai


  if event.key is 'enter':



In [6]:
K = 2
EP = 0.09

In [7]:
processor = WhisperProcessor.from_pretrained("openai/whisper-tiny")
model = WhisperForConditionalGeneration.from_pretrained(
        "openai/whisper-tiny").to('cuda')


The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(



preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.48M [00:00<?, ?B/s]

...

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.98k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/151M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.75k [00:00<?, ?B/s]

In [8]:
with tempfile.NamedTemporaryFile() as audtmp:
  video_clip = VideoFileClip(video_file_name)

  video_clip.audio.write_audiofile(audtmp.name+'.flac', codec="flac")

  aud, sr = librosa.load(
            audtmp.name+'.flac', sr=16000)
aud_frames = librosa.util.frame(
    aud,
    frame_length=int((K+EP)*16000),
    hop_length=int((K+EP)*16000),
    axis=-1
).T


MoviePy - Writing audio in /tmp/tmpn5ulky27.flac


MoviePy - Done.


# New Section

In [9]:
transcription = []

def stamp_time(x):
    return strftime("%H:%M:%S", gmtime(x*K))

for i, frame in enumerate(aud_frames):
    inp = processor(
        [frame],
        sampling_rate=sr,
        return_tensors="pt"
    ).input_features.to("cuda")
    generated_ids = model.generate(
        inp
    )
    text = ''.join(
        processor.batch_decode(generated_ids, skip_special_tokens=True)
    )
    transcription.append(
            (i, stamp_time(i), stamp_time(i+1), text)
            )
    percent = i/len(aud_frames)

Due to a bug fix in https://github.com/huggingface/transformers/pull/28687 transcription using a multilingual Whisper will default to language detection followed by transcription instead of translation to English.This might be a breaking change for your use case. If you want to instead always translate your audio to English, make sure to pass `language='en'`.
Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


In [10]:
srt = '\n\n'.join(list(map(
  lambda v: f"{v[0]+1}\n{v[1]},000 --> {v[2]},000\n{v[3].strip()}",
  transcription
)))


transcription = ' '.join(list(map(lambda z: z[-1], transcription)))

In [11]:
with open('video.srt', 'w') as f:
  f.write(srt)

In [12]:
with open(video_file_name, 'rb') as f:
  vid = f.read()
  data_url = "data:video/mp4;base64," + b64encode(vid).decode()

caption_base64 = "data:text/plain;base64,"+b64encode(srt.encode('utf-8')).decode()

video_html = f"""
<video width="640" height="360" controls>
    <source src="{data_url}" type="video/mp4">
    <track label="English" kind="subtitles" srclang="en" src="{caption_base64}" default>
</video>
"""

HTML(video_html)

In [15]:
genai.configure(api_key=userdata.get('GOOGLE_API_KEY'))
generation_config = genai.GenerationConfig(
        temperature=0.7
)

summ_model = genai.GenerativeModel(
    'gemini-1.5-pro-latest',
    generation_config=generation_config)

prompt = f"""The following text is a auto generated caption\
                of a video. It may have misspelt words. Read them very\
                carefully and summarize it into crisp points

                {transcription}
                """
res = summ_model.generate_content(prompt)

In [16]:
print(res.text)

* Recounts a memory from the 2011 Cricket World Cup final.
* The narrator and a friend (Raju) were in the stadium with 10-15 runs needed.
* The crowd spontaneously began singing the patriotic song "Vande Mataram" (misspelled as "one day matrim/matrimand").
* The singing started in the North Stand and spread throughout the stadium, emotionally moving the narrator and creating a powerful atmosphere with 35-40,000 people singing.

